# Titanic FeatureTools version

Follow this instruction: https://www.kaggle.com/vbmokin/titanic-featuretools-automatic-fe-fs

## Summary

(1) The first step is to automatic create a entity based on the combined df (traindf + testdf)

```es = ft.EntitySet(id = 'titanic_data')```

```es = es.entity_from_dataframe(entity_id = 'df', dataframe = df.drop(['Survived'], axis=1), 
                              variable_types = 
                              {
                                  'Embarked': ft.variable_types.Categorical,
                                  'Sex': ft.variable_types.Boolean,
                                  'Title': ft.variable_types.Categorical,
                                  'Family_Size': ft.variable_types.Numeric,
                                  'LastName': ft.variable_types.Categorical
                              },
                              index = 'PassengerId')```

(2) The second step: automatic feature engineering: 

```features, feature_names = ft.dfs(entityset = es, 
                                 target_entity = 'df', 
                                 max_depth = 2)```


(3) Feature selection

- correlation threshold
- SelectFromModel with Linear SVC
- SelectFromModel with Lasso
- SelectBest with Chi-2
- Recursive Feature Elimination (RFE) with Logistic Regression
- RFE with Random Forest

(4) Modeling (random forest)

In [2]:
import pandas as pd
import numpy as np 
import matplotlib.pyplot as plt
%matplotlib inline

import featuretools as ft
from featuretools.primitives import *
from featuretools.variable_types import Numeric

from sklearn.preprocessing import LabelEncoder, MinMaxScaler
from sklearn.linear_model import LinearRegression, LogisticRegression, LassoCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn.metrics import explained_variance_score
from sklearn.svm import LinearSVC
from sklearn.feature_selection import SelectFromModel, SelectKBest, RFE, chi2

# model tuning
from hyperopt import STATUS_OK, Trials, fmin, hp, tpe, space_eval

import warnings
warnings.filterwarnings("ignore")

In [3]:
traindf = pd.read_csv('titanic/train.csv').set_index('PassengerId')
testdf = pd.read_csv('titanic/test.csv').set_index('PassengerId')
df = pd.concat([traindf, testdf], axis=0, sort=False)

In [4]:
traindf

Survived  Pclass  \
PassengerId                     
1                   0       3   
2                   1       1   
3                   1       3   
4                   1       1   
5                   0       3   
...               ...     ...   
887                 0       2   
888                 1       1   
889                 0       3   
890                 1       1   
891                 0       3   

                                                          Name     Sex   Age  \
PassengerId                                                                    
1                                      Braund, Mr. Owen Harris    male  22.0   
2            Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0   
3                                       Heikkinen, Miss. Laina  female  26.0   
4                 Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0   
5                                     Allen, Mr. William Henry    male  35.0   
...                                                        ...     ...   ...   
887                                      Montvila, Rev. Juozas    male  27.0   
888                               Graham, Miss. Margaret Edith  female  19.0   
889                   Johnston, Miss. Catherine Helen "Carrie"  female   NaN   
890                                      Behr, Mr. Karl Howell    male  26.0   
891                                        Dooley, Mr. Patrick    male  32.0   

             SibSp  Parch            Ticket     Fare Cabin Embarked  
PassengerId                                                          
1                1      0         A/5 21171   7.2500   NaN        S  
2                1      0          PC 17599  71.2833   C85        C  
3                0      0  STON/O2. 3101282   7.9250   NaN        S  
4                1      0            113803  53.1000  C123        S  
5                0      0            373450   8.0500   NaN        S  
...            ...    ...               ...      ...   ...      ...  
887              0      0            211536  13.0000   NaN        S  
888              0      0            112053  30.0000   B42        S  
889              1      2        W./C. 6607  23.4500   NaN        S  
890              0      0            111369  30.0000  C148        C  
891              0      0            370376   7.7500   NaN        Q  

[891 rows x 11 columns]

## Preparing to modeling with manual FE

In [10]:
#Thanks to:
# https://www.kaggle.com/mauricef/titanic
# https://www.kaggle.com/vbmokin/titanic-top-3-one-line-of-the-prediction-code
#
df = pd.concat([traindf, testdf], axis=0, sort=False)
df['Title'] = df.Name.str.split(',').str[1].str.split('.').str[0].str.strip()
df['Title'] = df.Name.str.split(',').str[1].str.split('.').str[0].str.strip()
df['IsWomanOrBoy'] = ((df.Title == 'Master') | (df.Sex == 'female'))
df['LastName'] = df.Name.str.split(',').str[0]
family = df.groupby(df.LastName).Survived
df['WomanOrBoyCount'] = family.transform(lambda s: s[df.IsWomanOrBoy].fillna(0).count())
#df['WomanOrBoyCount'] = df.mask(df.IsWomanOrBoy, df.WomanOrBoyCount - 1, axis=0)
df['FamilySurvivedCount'] = family.transform(lambda s: s[df.IsWomanOrBoy].fillna(0).sum())
#df['FamilySurvivedCount'] = df.mask(df.IsWomanOrBoy, df.FamilySurvivedCount - \
                                    #df.Survived.fillna(0), axis=0)
df['WomanOrBoySurvived'] = df.FamilySurvivedCount / df.WomanOrBoyCount.replace(0, np.nan)
df.WomanOrBoyCount = df.WomanOrBoyCount.replace(np.nan, 0)
df['Alone'] = (df.WomanOrBoyCount == 0)

#Thanks to https://www.kaggle.com/kpacocha/top-6-titanic-machine-learning-from-disaster
#"Title" improvement
df['Title'] = df['Title'].replace('Ms','Miss')
df['Title'] = df['Title'].replace('Mlle','Miss')
df['Title'] = df['Title'].replace('Mme','Mrs')
# Embarked
df['Embarked'] = df['Embarked'].fillna('S')
# Cabin, Deck
df['Deck'] = df['Cabin'].apply(lambda s: s[0] if pd.notnull(s) else 'M')
df.loc[(df['Deck'] == 'T'), 'Deck'] = 'A'

# Thanks to https://www.kaggle.com/erinsweet/simpledetect
# Fare
med_fare = df.groupby(['Pclass', 'Parch', 'SibSp']).Fare.median()[3][0][0]
df['Fare'] = df['Fare'].fillna(med_fare)
#Age
df['Age'] = df.groupby(['Sex', 'Pclass', 'Title'])['Age'].apply(lambda x: x.fillna(x.median()))
# Family_Size
df['Family_Size'] = df['SibSp'] + df['Parch'] + 1

# Thanks to https://www.kaggle.com/vbmokin/titanic-top-3-cluster-analysis
cols_to_drop = ['Name','Ticket','Cabin']
df = df.drop(cols_to_drop, axis=1)

df.WomanOrBoySurvived = df.WomanOrBoySurvived.fillna(0)
df.WomanOrBoyCount = df.WomanOrBoyCount.fillna(0)
df.FamilySurvivedCount = df.FamilySurvivedCount.fillna(0)
df.Alone = df.Alone.fillna(0)
df.Alone = df.Alone*1

In [11]:
df

Survived  Pclass     Sex   Age  SibSp  Parch      Fare Embarked  \
PassengerId                                                                    
1                 0.0       3    male  22.0      1      0    7.2500        S   
2                 1.0       1  female  38.0      1      0   71.2833        C   
3                 1.0       3  female  26.0      0      0    7.9250        S   
4                 1.0       1  female  35.0      1      0   53.1000        S   
5                 0.0       3    male  35.0      0      0    8.0500        S   
...               ...     ...     ...   ...    ...    ...       ...      ...   
1305              NaN       3    male  26.0      0      0    8.0500        S   
1306              NaN       1  female  39.0      0      0  108.9000        C   
1307              NaN       3    male  38.5      0      0    7.2500        S   
1308              NaN       3    male  26.0      0      0    8.0500        S   
1309              NaN       3    male   6.0      1      1   22.3583        C   

              Title  IsWomanOrBoy       LastName  WomanOrBoyCount  \
PassengerId                                                         
1                Mr         False         Braund                0   
2               Mrs          True        Cumings                1   
3              Miss          True      Heikkinen                1   
4               Mrs          True       Futrelle                1   
5                Mr         False          Allen                1   
...             ...           ...            ...              ...   
1305             Mr         False        Spector                0   
1306           Dona          True  Oliva y Ocana                1   
1307             Mr         False        Saether                0   
1308             Mr         False           Ware                1   
1309         Master          True          Peter                3   

             FamilySurvivedCount  WomanOrBoySurvived  Alone Deck  Family_Size  
PassengerId                                                                    
1                            0.0            0.000000      1    M            2  
2                            1.0            1.000000      0    C            2  
3                            1.0            1.000000      0    M            1  
4                            1.0            1.000000      0    C            2  
5                            1.0            1.000000      0    M            1  
...                          ...                 ...    ...  ...          ...  
1305                         0.0            0.000000      1    M            1  
1306                         0.0            0.000000      0    C            1  
1307                         0.0            0.000000      1    M            1  
1308                         0.0            0.000000      0    M            1  
1309                         2.0            0.666667      0    M            3  

[1309 rows x 17 columns]

In [12]:
df_optimum = pd.concat([df.WomanOrBoySurvived.fillna(0), df.Alone, df.Sex.replace({'male': 0, 'female': 1})], axis=1)

In [13]:
target = df.Survived.loc[traindf.index]
df = df.drop(['SibSp','Parch','IsWomanOrBoy','WomanOrBoyCount','FamilySurvivedCount','WomanOrBoySurvived','Alone'], axis=1)
df['PassengerId'] = df.index
df.head()

Survived  Pclass     Sex   Age     Fare Embarked Title  \
PassengerId                                                           
1                 0.0       3    male  22.0   7.2500        S    Mr   
2                 1.0       1  female  38.0  71.2833        C   Mrs   
3                 1.0       3  female  26.0   7.9250        S  Miss   
4                 1.0       1  female  35.0  53.1000        S   Mrs   
5                 0.0       3    male  35.0   8.0500        S    Mr   

              LastName Deck  Family_Size  PassengerId  
PassengerId                                            
1               Braund    M            2            1  
2              Cumings    C            2            2  
3            Heikkinen    M            1            3  
4             Futrelle    C            2            4  
5                Allen    M            1            5

# Automatic FE with Featuretools

In [14]:
es = ft.EntitySet(id = 'titanic_data')
es = es.entity_from_dataframe(entity_id = 'df', dataframe = df.drop(['Survived'], axis=1), 
                              variable_types = 
                              {
                                  'Embarked': ft.variable_types.Categorical,
                                  'Sex': ft.variable_types.Boolean,
                                  'Title': ft.variable_types.Categorical,
                                  'Family_Size': ft.variable_types.Numeric,
                                  'LastName': ft.variable_types.Categorical
                              },
                              index = 'PassengerId')

In [18]:
es['df']

Entity: df
  Variables:
    PassengerId (dtype: index)
    Pclass (dtype: numeric)
    Age (dtype: numeric)
    Fare (dtype: numeric)
    Deck (dtype: categorical)
    Embarked (dtype: categorical)
    Sex (dtype: boolean)
    Title (dtype: categorical)
    Family_Size (dtype: numeric)
    LastName (dtype: categorical)
  Shape:
    (Rows: 1309, Columns: 10)

In [19]:
es['df'].df

PassengerId  Pclass   Age      Fare Deck Embarked     Sex   Title  \
1               1       3  22.0    7.2500    M        S    male      Mr   
2               2       1  38.0   71.2833    C        C  female     Mrs   
3               3       3  26.0    7.9250    M        S  female    Miss   
4               4       1  35.0   53.1000    C        S  female     Mrs   
5               5       3  35.0    8.0500    M        S    male      Mr   
...           ...     ...   ...       ...  ...      ...     ...     ...   
1305         1305       3  26.0    8.0500    M        S    male      Mr   
1306         1306       1  39.0  108.9000    C        C  female    Dona   
1307         1307       3  38.5    7.2500    M        S    male      Mr   
1308         1308       3  26.0    8.0500    M        S    male      Mr   
1309         1309       3   6.0   22.3583    M        C    male  Master   

      Family_Size       LastName  
1               2         Braund  
2               2        Cumings  
3               1      Heikkinen  
4               2       Futrelle  
5               1          Allen  
...           ...            ...  
1305            1        Spector  
1306            1  Oliva y Ocana  
1307            1        Saether  
1308            1           Ware  
1309            3          Peter  

[1309 rows x 10 columns]

In [20]:
es = es.normalize_entity(base_entity_id='df', new_entity_id='Pclass', index='Pclass')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Sex', index='Sex')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Age', index='Age')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Fare', index='Fare')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Embarked', index='Embarked')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Title', index='Title')
es = es.normalize_entity(base_entity_id='df', new_entity_id='LastName', index='LastName')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Deck', index='Deck')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Family_Size', index='Family_Size')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Title_Sex', index='Sex')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Sex_LastName', index='LastName')
es = es.normalize_entity(base_entity_id='df', new_entity_id='Title_LastName', index='LastName')
es

Entityset: titanic_data
  Entities:
    df [Rows: 1309, Columns: 10]
    Pclass [Rows: 3, Columns: 1]
    Sex [Rows: 2, Columns: 1]
    Age [Rows: 99, Columns: 1]
    Fare [Rows: 281, Columns: 1]
    Embarked [Rows: 3, Columns: 1]
    Title [Rows: 15, Columns: 1]
    LastName [Rows: 875, Columns: 1]
    Deck [Rows: 8, Columns: 1]
    Family_Size [Rows: 9, Columns: 1]
    Title_Sex [Rows: 2, Columns: 1]
    Sex_LastName [Rows: 875, Columns: 1]
    Title_LastName [Rows: 875, Columns: 1]
  Relationships:
    df.Pclass -> Pclass.Pclass
    df.Sex -> Sex.Sex
    df.Age -> Age.Age
    df.Fare -> Fare.Fare
    df.Embarked -> Embarked.Embarked
    df.Title -> Title.Title
    df.LastName -> LastName.LastName
    df.Deck -> Deck.Deck
    df.Family_Size -> Family_Size.Family_Size
    df.Sex -> Title_Sex.Sex
    df.LastName -> Sex_LastName.LastName
    df.LastName -> Title_LastName.LastName

In [23]:
es['Pclass'].df

Pclass
3       3
1       1
2       2

In [24]:
es['Age'].df

Age
22.00  22.00
38.00  38.00
26.00  26.00
35.00  35.00
54.00  54.00
...      ...
60.50  60.50
11.50  11.50
0.33    0.33
0.17    0.17
38.50  38.50

[99 rows x 1 columns]

In [25]:
es['Sex'].df

Sex
male      male
female  female

In [26]:
primitives = ft.list_primitives()
pd.options.display.max_colwidth = 500
primitives[primitives['type'] == 'aggregation'].head(primitives[primitives['type'] == 'aggregation'].shape[0])

name         type  dask_compatible  koalas_compatible  \
0              first  aggregation            False              False   
1               skew  aggregation            False              False   
2      n_most_common  aggregation            False              False   
3         num_unique  aggregation             True               True   
4   time_since_first  aggregation            False              False   
5                all  aggregation             True              False   
6                min  aggregation             True               True   
7               last  aggregation            False              False   
8               mean  aggregation             True               True   
9       percent_true  aggregation             True              False   
10           entropy  aggregation            False              False   
11               std  aggregation             True               True   
12            median  aggregation            False              False   
13  avg_time_between  aggregation            False              False   
14               sum  aggregation             True               True   
15             count  aggregation             True               True   
16          num_true  aggregation             True              False   
17             trend  aggregation            False              False   
18               max  aggregation             True               True   
19   time_since_last  aggregation            False              False   
20               any  aggregation             True              False   
21              mode  aggregation            False              False   

                                                                        description  \
0                                             Determines the first value in a list.   
1   Computes the extent to which a distribution differs from a normal distribution.   
2                                          Determines the `n` most common elements.   
3                  Determines the number of distinct values, ignoring `NaN` values.   
4                Calculates the time elapsed since the first datetime (in seconds).   
5                                    Calculates if all values are 'True' in a list.   
6                             Calculates the smallest value, ignoring `NaN` values.   
7                                              Determines the last value in a list.   
8                                        Computes the average for a list of values.   
9                                          Determines the percent of `True` values.   
10                                Calculates the entropy for a categorical variable   
11              Computes the dispersion relative to the mean value, ignoring `NaN`.   
12                            Determines the middlemost number in a list of values.   
13               Computes the average number of seconds between consecutive events.   
14                                   Calculates the total addition, ignoring `NaN`.   
15                          Determines the total number of values, excluding `NaN`.   
16                                              Counts the number of `True` values.   
17                                    Calculates the trend of a variable over time.   
18                             Calculates the highest value, ignoring `NaN` values.   
19        Calculates the time elapsed since the last datetime (default in seconds).   
20                                     Determines if any value is 'True' in a list.   
21                                     Determines the most commonly repeated value.   

                  valid_inputs return_type  
0                     Variable        None  
1                      Numeric     Numeric  
2                     Discrete    Discrete  
3                     Discrete     Numeric  
4            DatetimeTimeIndex     Numeric  
5                      Boolean     Boolean  
6                  

In [27]:
features, feature_names = ft.dfs(entityset = es, 
                                 target_entity = 'df', 
                                 max_depth = 2)
len(feature_names)

213

In [28]:
feature_names

[<Feature: Pclass>,
 <Feature: Age>,
 <Feature: Fare>,
 <Feature: Deck>,
 <Feature: Embarked>,
 <Feature: Sex>,
 <Feature: Title>,
 <Feature: Family_Size>,
 <Feature: LastName>,
 <Feature: Pclass.COUNT(df)>,
 <Feature: Pclass.MODE(df.Age)>,
 <Feature: Pclass.MODE(df.Deck)>,
 <Feature: Pclass.MODE(df.Embarked)>,
 <Feature: Pclass.MODE(df.Family_Size)>,
 <Feature: Pclass.MODE(df.Fare)>,
 <Feature: Pclass.MODE(df.LastName)>,
 <Feature: Pclass.MODE(df.Sex)>,
 <Feature: Pclass.MODE(df.Title)>,
 <Feature: Pclass.NUM_UNIQUE(df.Age)>,
 <Feature: Pclass.NUM_UNIQUE(df.Deck)>,
 <Feature: Pclass.NUM_UNIQUE(df.Embarked)>,
 <Feature: Pclass.NUM_UNIQUE(df.Family_Size)>,
 <Feature: Pclass.NUM_UNIQUE(df.Fare)>,
 <Feature: Pclass.NUM_UNIQUE(df.LastName)>,
 <Feature: Pclass.NUM_UNIQUE(df.Sex)>,
 <Feature: Pclass.NUM_UNIQUE(df.Title)>,
 <Feature: Sex.COUNT(df)>,
 <Feature: Sex.MODE(df.Age)>,
 <Feature: Sex.MODE(df.Deck)>,
 <Feature: Sex.MODE(df.Embarked)>,
 <Feature: Sex.MODE(df.Family_Size)>,
 <Feature: 

In [29]:
features

Pclass   Age      Fare Deck Embarked     Sex   Title  \
PassengerId                                                         
1                 3  22.0    7.2500    M        S    male      Mr   
2                 1  38.0   71.2833    C        C  female     Mrs   
3                 3  26.0    7.9250    M        S  female    Miss   
4                 1  35.0   53.1000    C        S  female     Mrs   
5                 3  35.0    8.0500    M        S    male      Mr   
...             ...   ...       ...  ...      ...     ...     ...   
1305              3  26.0    8.0500    M        S    male      Mr   
1306              1  39.0  108.9000    C        C  female    Dona   
1307              3  38.5    7.2500    M        S    male      Mr   
1308              3  26.0    8.0500    M        S    male      Mr   
1309              3   6.0   22.3583    M        C    male  Master   

             Family_Size       LastName  Pclass.COUNT(df)  ...  \
PassengerId                                                ...   
1                      2         Braund               709  ...   
2                      2        Cumings               323  ...   
3                      1      Heikkinen               709  ...   
4                      2       Futrelle               323  ...   
5                      1          Allen               709  ...   
...                  ...            ...               ...  ...   
1305                   1        Spector               709  ...   
1306                   1  Oliva y Ocana               323  ...   
1307                   1        Saether               709  ...   
1308                   1           Ware               709  ...   
1309                   3          Peter               709  ...   

             Title_LastName.MODE(df.Sex) Title_LastName.MODE(df.Title)  \
PassengerId                                                              
1                                   male                            Mr   
2                                 female                            Mr   
3                                 female                          Miss   
4                                 female                            Mr   
5                                 female                          Miss   
...                                  ...                           ...   
1305                                male                            Mr   
1306                              female                          Dona   
1307                                male                            Mr   
1308                                male                            Mr   
1309                              female                        Master   

            Title_LastName.NUM_UNIQUE(df.Age)  \
PassengerId                                     
1                                           2   
2                                           2   
3                                           1   
4                                           2   
5                                           2   
...                                       ...   
1305                                        1   
1306                                        1   
1307                                        1   
1308                                        4   
1309                                        3   

             Title_LastName.NUM_UNIQUE(df.Deck)  \
PassengerId                                       
1                                             1   
2                                             1   
3                                             1   
4                                             1   
5                                             2   
...                                         ...   
1305                                          1   
1306                                          1   
1307                                          1   
1308                                          1   
1309                                       

## Encoding categorical features

In [30]:
# Determination categorical features
numerics = ['int8', 'int16', 'int32', 'int64', 'float16', 'float32', 'float64']
categorical_columns = []
cols = features.columns.values.tolist()
for col in cols:
    if features[col].dtype in numerics: continue
    categorical_columns.append(col)
categorical_columns

['Deck',
 'Embarked',
 'Sex',
 'Title',
 'LastName',
 'Pclass.MODE(df.Deck)',
 'Pclass.MODE(df.Embarked)',
 'Pclass.MODE(df.LastName)',
 'Pclass.MODE(df.Sex)',
 'Pclass.MODE(df.Title)',
 'Sex.MODE(df.Deck)',
 'Sex.MODE(df.Embarked)',
 'Sex.MODE(df.LastName)',
 'Sex.MODE(df.Title)',
 'Age.MODE(df.Deck)',
 'Age.MODE(df.Embarked)',
 'Age.MODE(df.LastName)',
 'Age.MODE(df.Sex)',
 'Age.MODE(df.Title)',
 'Fare.MODE(df.Deck)',
 'Fare.MODE(df.Embarked)',
 'Fare.MODE(df.LastName)',
 'Fare.MODE(df.Sex)',
 'Fare.MODE(df.Title)',
 'Embarked.MODE(df.Deck)',
 'Embarked.MODE(df.LastName)',
 'Embarked.MODE(df.Sex)',
 'Embarked.MODE(df.Title)',
 'Title.MODE(df.Deck)',
 'Title.MODE(df.Embarked)',
 'Title.MODE(df.LastName)',
 'Title.MODE(df.Sex)',
 'LastName.MODE(df.Deck)',
 'LastName.MODE(df.Embarked)',
 'LastName.MODE(df.Sex)',
 'LastName.MODE(df.Title)',
 'Deck.MODE(df.Embarked)',
 'Deck.MODE(df.LastName)',
 'Deck.MODE(df.Sex)',
 'Deck.MODE(df.Title)',
 'Family_Size.MODE(df.Deck)',
 'Family_Size.MODE(

In [31]:
# Encoding categorical features
for col in categorical_columns:
    if col in features.columns:
        le = LabelEncoder()
        le.fit(list(features[col].astype(str).values))
        features[col] = le.transform(list(features[col].astype(str).values))

In [32]:
features.head(3)

Pclass   Age     Fare  Deck  Embarked  Sex  Title  Family_Size  \
PassengerId                                                                   
1                 3  22.0   7.2500     7         2    1     10            2   
2                 1  38.0  71.2833     2         0    0     11            2   
3                 3  26.0   7.9250     7         2    0      9            1   

             LastName  Pclass.COUNT(df)  ...  Title_LastName.MODE(df.Sex)  \
PassengerId                              ...                                
1                 100               709  ...                            1   
2                 182               323  ...                            0   
3                 329               709  ...                            0   

             Title_LastName.MODE(df.Title)  Title_LastName.NUM_UNIQUE(df.Age)  \
PassengerId                                                                     
1                                       10                                  2   
2                                       10                                  2   
3                                        9                                  1   

             Title_LastName.NUM_UNIQUE(df.Deck)  \
PassengerId                                       
1                                             1   
2                                             1   
3                                             1   

             Title_LastName.NUM_UNIQUE(df.Embarked)  \
PassengerId                                           
1                                                 1   
2                                                 1   
3                                                 1   

             Title_LastName.NUM_UNIQUE(df.Family_Size)  \
PassengerId                                              
1                                                    1   
2                                                    1   
3                                                    1   

             Title_LastName.NUM_UNIQUE(df.Fare)  \
PassengerId                                       
1                                             2   
2                                             1   
3                                             1   

             Title_LastName.NUM_UNIQUE(df.Pclass)  \
PassengerId                                         
1                                               1   
2                                               1   
3                                               1   

             Title_LastName.NUM_UNIQUE(df.Sex)  \
PassengerId                                      
1                                            1   
2                                            2   
3                                            1   

             Title_LastName.NUM_UNIQUE(df.Title)  
PassengerId                                       
1                                              1  
2                                              2  
3                                              1  

[3 rows x 213 columns]

## Automatic feature selection (FS)

In [33]:
train, test = features.loc[traindf.index], features.loc[testdf.index]
X_norm = MinMaxScaler().fit_transform(train)

In [36]:
test

Pclass   Age      Fare  Deck  Embarked  Sex  Title  Family_Size  \
PassengerId                                                                    
892               3  34.5    7.8292     7         1    1     10            1   
893               3  47.0    7.0000     7         2    0     11            2   
894               2  62.0    9.6875     7         1    1     10            1   
895               3  27.0    8.6625     7         2    1     10            1   
896               3  22.0   12.2875     7         2    0     11            3   
...             ...   ...       ...   ...       ...  ...    ...          ...   
1305              3  26.0    8.0500     7         2    1     10            1   
1306              1  39.0  108.9000     2         0    0      3            1   
1307              3  38.5    7.2500     7         2    1     10            1   
1308              3  26.0    8.0500     7         2    1     10            1   
1309              3   6.0   22.3583     7         0    1      8            3   

             LastName  Pclass.COUNT(df)  ...  Title_LastName.MODE(df.Sex)  \
PassengerId                              ...                                
892               401               709  ...                            0   
893               846               709  ...                            0   
894               552               277  ...                            1   
895               854               709  ...                            1   
896               342               709  ...                            0   
...               ...               ...  ...                          ...   
1305              753               709  ...                            1   
1306              593               323  ...                            0   
1307              699               709  ...                            1   
1308              827               709  ...                            1   
1309              634               709  ...                            0   

             Title_LastName.MODE(df.Title)  Title_LastName.NUM_UNIQUE(df.Age)  \
PassengerId                                                                     
892                                      9                                  4   
893                                     11                                  1   
894                                     10                                  1   
895                                     10                                  1   
896                                      9                                  2   
...                                    ...                                ...   
1305                                    10                                  1   
1306                                     3                                  1   
1307                                    10                                  1   
1308                                    10                                  4   
1309                                     8                                  3   

             Title_LastName.NUM_UNIQUE(df.Deck)  \
PassengerId                                       
892                                           1   
893                                           1   
894                                           1   
895                                           1   
896                                           1   
...                                         ...   
1305                                          1   
1306                                          1   
1307                                          1   
1308                                          1   
1309                                          2   

             Title_LastName.NUM_UNIQUE(df.Embarked)  \
PassengerId                                           
892                                               2   
893                                               1   
894                             

In [37]:
# Threshold for removing correlated variables
threshold = 0.9

def highlight(value):
    if value > threshold:
        style = 'background-color: pink'
    else:
        style = 'background-color: palegreen'
    return style

# Absolute value correlation matrix
corr_matrix = features.corr().abs()
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(np.bool))
upper.style.applymap(highlight)

In [38]:
# Select columns with correlations above threshold
collinear_features = [column for column in upper.columns if any(upper[column] > threshold)]
features_filtered = features.drop(columns = collinear_features)
#features_positive = features_filtered.loc[:, features_filtered.ge(0).all()]
print('The number of features that passed the collinearity threshold: ', features_filtered.shape[1])

The number of features that passed the collinearity threshold:  107


In [39]:
FE_option0 = features.columns
FE_option1 = features_filtered.columns
print(len(FE_option0), len(FE_option1))

213 107


## FS by the SelectFromModel with LinearSVC

In [40]:
lsvc = LinearSVC(C=0.01, penalty="l1", dual=False).fit(train, target)
model = SelectFromModel(lsvc, prefit=True)
X_new = model.transform(train)
X_selected_df = pd.DataFrame(X_new, columns=[train.columns[i] for i in range(len(train.columns)) if model.get_support()[i]])
X_selected_df.shape

(891, 39)

In [44]:
model.get_support()

array([False,  True,  True, False, False, False, False, False,  True,
        True,  True, False, False, False, False, False, False, False,
        True, False, False, False, False,  True, False, False,  True,
       False, False, False, False, False, False, False, False, False,
       False, False, False,  True,  True, False, False,  True, False,
       False, False, False,  True, False, False, False, False, False,
       False, False, False, False, False, False,  True,  True, False,
       False, False,  True, False, False, False, False, False, False,
       False, False, False, False, False,  True, False, False, False,
       False, False, False, False, False,  True, False, False, False,
        True, False, False, False,  True,  True, False, False, False,
        True, False, False, False,  True, False, False, False,  True,
        True, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False,

In [45]:
FE_option2 = X_selected_df.columns
FE_option2

Index(['Age', 'Fare', 'LastName', 'Pclass.COUNT(df)', 'Pclass.MODE(df.Age)',
       'Pclass.NUM_UNIQUE(df.Age)', 'Pclass.NUM_UNIQUE(df.LastName)',
       'Sex.COUNT(df)', 'Sex.NUM_UNIQUE(df.Fare)',
       'Sex.NUM_UNIQUE(df.LastName)', 'Age.COUNT(df)', 'Age.MODE(df.LastName)',
       'Fare.COUNT(df)', 'Fare.MODE(df.Age)', 'Fare.MODE(df.LastName)',
       'Embarked.COUNT(df)', 'Embarked.NUM_UNIQUE(df.Age)',
       'Embarked.NUM_UNIQUE(df.LastName)', 'Title.COUNT(df)',
       'Title.MODE(df.Age)', 'Title.MODE(df.Fare)', 'Title.NUM_UNIQUE(df.Age)',
       'Title.NUM_UNIQUE(df.Fare)', 'Title.NUM_UNIQUE(df.LastName)',
       'Deck.COUNT(df)', 'Deck.MODE(df.Fare)', 'Deck.NUM_UNIQUE(df.Age)',
       'Deck.NUM_UNIQUE(df.LastName)', 'Family_Size.COUNT(df)',
       'Family_Size.MODE(df.Age)', 'Family_Size.MODE(df.Fare)',
       'Family_Size.NUM_UNIQUE(df.Age)', 'Family_Size.NUM_UNIQUE(df.LastName)',
       'Title_Sex.COUNT(df)', 'Title_Sex.NUM_UNIQUE(df.Fare)',
       'Title_Sex.NUM_UNIQUE(df.La

## FS by the SelectFromModel with Lasso

In [46]:
lasso = LassoCV(cv=5).fit(train, target)
model = SelectFromModel(lasso, prefit=True)
X_new = model.transform(train)
X_selected_df = pd.DataFrame(X_new, columns=[train.columns[i] for i in range(len(train.columns)) 
                                             if model.get_support()[i]])

In [47]:
FE_option3 = X_selected_df.columns
FE_option3

Index(['Age', 'Fare', 'LastName', 'Pclass.COUNT(df)',
       'Pclass.NUM_UNIQUE(df.Fare)', 'Sex.COUNT(df)', 'Age.COUNT(df)',
       'Age.MODE(df.LastName)', 'Fare.COUNT(df)', 'Fare.MODE(df.Age)',
       'Fare.MODE(df.LastName)', 'Embarked.COUNT(df)', 'Title.COUNT(df)',
       'Title.MODE(df.Age)', 'Title.MODE(df.Fare)',
       'Title.NUM_UNIQUE(df.Fare)', 'Title.NUM_UNIQUE(df.LastName)',
       'Deck.COUNT(df)', 'Deck.MODE(df.Fare)', 'Family_Size.MODE(df.Age)',
       'Family_Size.MODE(df.Fare)', 'Family_Size.NUM_UNIQUE(df.Age)',
       'Family_Size.NUM_UNIQUE(df.LastName)'],
      dtype='object')

In [48]:
X_selected_df

Age     Fare  LastName  Pclass.COUNT(df)  Pclass.NUM_UNIQUE(df.Fare)  \
0    22.0   7.2500     100.0             709.0                       133.0   
1    38.0  71.2833     182.0             323.0                       107.0   
2    26.0   7.9250     329.0             709.0                       133.0   
3    35.0  53.1000     267.0             323.0                       107.0   
4    35.0   8.0500      15.0             709.0                       133.0   
..    ...      ...       ...               ...                         ...   
886  27.0  13.0000     535.0             277.0                        48.0   
887  19.0  30.0000     294.0             323.0                       107.0   
888  18.0  23.4500     383.0             709.0                       133.0   
889  26.0  30.0000      69.0             323.0                       107.0   
890  32.0   7.7500     214.0             709.0                       133.0   

     Sex.COUNT(df)  Age.COUNT(df)  Age.MODE(df.LastName)  Fare.COUNT(df)  \
0            843.0           43.0                   21.0            18.0   
1            466.0           14.0                    9.0             2.0   
2            466.0          166.0                   69.0            23.0   
3            466.0           23.0                    1.0             6.0   
4            843.0           23.0                    1.0            60.0   
..             ...            ...                    ...             ...   
886          843.0           30.0                    9.0            59.0   
887          466.0           29.0                    7.0             7.0   
888          466.0           87.0                   69.0             4.0   
889          843.0          166.0                   69.0             7.0   
890          843.0           24.0                    6.0            55.0   

     Fare.MODE(df.Age)  ...  Title.MODE(df.Age)  Title.MODE(df.Fare)  \
0                 22.0  ...                26.0                 8.05   
1                 38.0  ...                31.0                26.00   
2                 20.0  ...                18.0                 7.75   
3                 18.0  ...                31.0                26.00   
4                 26.0  ...                26.0                 8.05   
..                 ...  ...                 ...                  ...   
886               30.0  ...                27.0                13.00   
887               19.0  ...                18.0                 7.75   
888                6.0  ...                18.0                 7.75   
889               19.0  ...                26.0                 8.05   
890               26.0  ...                26.0                 8.05   

     Title.NUM_UNIQUE(df.Fare)  Title.NUM_UNIQUE(df.LastName)  Deck.COUNT(df)  \
0                        215.0                          650.0          1014.0   
1                        140.0                          194.0            94.0   
2                        129.0                          219.0          1014.0   
3                        140.0                          194.0            94.0   
4                        215.0                          650.0          1014.0   
..                         ...                            ...             ...   
886                        5.0                            8.0          1014.0   
887                      129.0                          219.0            65.0   
888                      129.0                          219.0          1014.0   
889                      215.0                          650.0            94.0   
890                      215.0                          650.0          1014.0   

     Deck.MODE(df.Fare)  Family_Size.MODE(df.Age)  Family_Size.MODE(df.Fare)  \
0                 8.050                      26.0                    26.0000   
1               263.000                      26.0                    26.0000   
2                 8.050                      26.0                     8.0500  

## FS by the SelectKBest with Chi-2

In [49]:
# Visualization from https://towardsdatascience.com/feature-selection-techniques-in-machine-learning-with-python-f24e7da3f36e
# but to k='all'
bestfeatures = SelectKBest(score_func=chi2, k='all')
fit = bestfeatures.fit(train, target)
dfscores = pd.DataFrame(fit.scores_)
dfcolumns = pd.DataFrame(train.columns)
#concat two dataframes for better visualization 
featureScores = pd.concat([dfcolumns,dfscores],axis=1)
featureScores.columns = ['Feature','Score']  #naming the dataframe columns
print(featureScores.nlargest(len(dfcolumns),'Score')) 

                               Feature         Score
94                     Title.COUNT(df)  35488.726510
108      Title.NUM_UNIQUE(df.LastName)  29591.581330
128                     Deck.COUNT(df)  18118.376846
141       Deck.NUM_UNIQUE(df.LastName)  12352.761769
26                       Sex.COUNT(df)  12015.112823
..                                 ...           ...
37         Sex.NUM_UNIQUE(df.Embarked)      0.000000
13         Pclass.MODE(df.Family_Size)      0.000000
160     Family_Size.NUM_UNIQUE(df.Sex)      0.000000
38      Sex.NUM_UNIQUE(df.Family_Size)      0.000000
173  Title_Sex.NUM_UNIQUE(df.Embarked)      0.000000

[201 rows x 2 columns]


In [50]:
FE_option4 = featureScores[featureScores['Score'] > 1000]['Feature']
len(FE_option4)

23

In [51]:
FE_option5 = featureScores[featureScores['Score'] > 100]['Feature']
len(FE_option5)

49

## FS by the Recursive Feature Elimination (RFE) with Logistic Regression

In [52]:
rfe_selector = RFE(estimator=LogisticRegression(), n_features_to_select=50, step=10, verbose=5)
rfe_selector.fit(X_norm, target)

Fitting estimator with 213 features.
Fitting estimator with 203 features.
Fitting estimator with 193 features.
Fitting estimator with 183 features.
Fitting estimator with 173 features.
Fitting estimator with 163 features.
Fitting estimator with 153 features.
Fitting estimator with 143 features.
Fitting estimator with 133 features.
Fitting estimator with 123 features.
Fitting estimator with 113 features.
Fitting estimator with 103 features.
Fitting estimator with 93 features.
Fitting estimator with 83 features.
Fitting estimator with 73 features.
Fitting estimator with 63 features.
Fitting estimator with 53 features.


RFE(estimator=LogisticRegression(), n_features_to_select=50, step=10, verbose=5)

In [53]:
rfe_selector.get_support()

array([False,  True,  True, False, False, False, False,  True, False,
       False, False, False, False, False, False,  True, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
        True, False, False, False, False, False, False, False, False,
        True, False, False,  True, False, False, False, False, False,
       False, False, False, False,  True, False,  True,  True,  True,
        True,  True,  True,  True, False, False, False,  True, False,
        True, False,  True, False, False, False, False, False, False,
       False,  True, False, False, False, False, False, False, False,
       False, False, False, False,  True,  True,  True, False,  True,
       False,  True, False, False, False,  True, False,  True,  True,
        True,  True, False, False, False, False, False, False, False,
       False, False, False,  True, False,  True, False, False, False,
       False, False,

In [54]:
rfe_support = rfe_selector.get_support()
rfe_feature = train.loc[:,rfe_support].columns.tolist()
print(str(len(rfe_feature)), 'selected features')

50 selected features


In [55]:
FE_option6 = rfe_feature

## FS by the Recursive Feature Elimination (RFE) with Random Forest

In [56]:
embeded_rf_selector = SelectFromModel(RandomForestClassifier(n_estimators=200), threshold='1.25*median')
embeded_rf_selector.fit(train, target)

SelectFromModel(estimator=RandomForestClassifier(n_estimators=200),
                threshold='1.25*median')

In [57]:
embeded_rf_support = embeded_rf_selector.get_support()
embeded_rf_feature = train.loc[:,embeded_rf_support].columns.tolist()
print(str(len(embeded_rf_feature)), 'selected features')

89 selected features


In [58]:
FE_option7 = embeded_rf_feature

# Modeling

## The Random Forest Classifiers for 8 options of selected feature sets

In [59]:
def RF (features_set,file):
    # Tuning Random Forest model for features "features_set", makes prediction and save it into file  
    train_fe = train[features_set]
    test_fe = test[features_set]
    random_forest = GridSearchCV(estimator=RandomForestClassifier(), param_grid={'n_estimators': [100, 500]}, cv=5).fit(train_fe, target)
    random_forest.fit(train_fe, target)
    Y_pred = random_forest.predict(test_fe).astype(int)
    random_forest.score(train_fe, target)
    acc_random_forest = round(random_forest.score(train_fe, target) * 100, 2)
    #pd.DataFrame({'Survived': Y_pred}, index=testdf.index).reset_index().to_csv(file, index=False)
    return acc_random_forest

In [60]:
acc0 = RF(FE_option0, 'survived_FT.csv')
acc1 = RF(FE_option1, 'survived_FE1_Pearson.csv')
acc2 = RF(FE_option2, 'survived_FE2_LinSVC.csv')
acc3 = RF(FE_option3, 'survived_FE3_Lasso.csv')
acc4 = RF(FE_option4, 'survived_FE4_Chi2_1000.csv')
acc5 = RF(FE_option5, 'survived_FE5_Chi2_100.csv')
acc6 = RF(FE_option6, 'survived_FE6_RFE_LogR.csv')
acc7 = RF(FE_option7, 'survived_FE7_RFE_RF.csv')

In [61]:
models = pd.DataFrame({
    'Model': ['FT',
              'FT + Pearson correlation', 
              'FT + SelectFromModel with LinearSVC',
              'FT + SelectFromModel with Lasso', 
              'FT + SelectKBest with Chi-2 with Score > 1000',
              'FT + SelectKBest with Chi-2 with Score > 100',
              'FT + RFE with Logistic Regression',
              'FT + RFE with Random Forest'],
    
    'acc':  [acc0, acc1, acc2, acc3, acc4, acc5, acc6, acc7]})

In [66]:
models

Model    acc
0                                             FT  99.89
1                       FT + Pearson correlation  99.89
2            FT + SelectFromModel with LinearSVC  99.89
3                FT + SelectFromModel with Lasso  99.89
4  FT + SelectKBest with Chi-2 with Score > 1000  98.88
5   FT + SelectKBest with Chi-2 with Score > 100  99.89
6              FT + RFE with Logistic Regression  98.88
7                    FT + RFE with Random Forest  99.89